In [22]:
import pandas as pd

df = pd.read_csv("/home/is/dwipraseetyo-a/NAS_HAI/Datasets/grpo_3modalities_datasets/train_balancediseaseaugment.csv")

In [3]:
%cd /home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni

/home/ldap-users-2/dwipraseetyo-a/Project/Qwen2.5-Omni


In [130]:
import soundfile as sf

from transformers import Qwen2_5OmniForConditionalGeneration, Qwen2_5OmniProcessor
from qwen_omni_utils import process_mm_info

processor = Qwen2_5OmniProcessor.from_pretrained("Qwen/Qwen2.5-Omni-7B")

conversation = [
    {
        "role": "system",
        "content": [
            {"type": "text", "text": "You are Qwen, a virtual human developed by the Qwen Team, Alibaba Group, capable of perceiving auditory and visual inputs, as well as generating text and speech."}
        ],
    },
    {
        "role": "user",
        "content": [
            {"type": "image", "image": "/home/is/dwipraseetyo-a/NAS_HAI/Datasets/grpo_3modalities_datasets/validation/35917_Da8Uymca1IpX3fAB.wav"},
            {"type": "audio", "audio": "/home/is/dwipraseetyo-a/NAS_HAI/Datasets/grpo_3modalities_datasets/validation/0AHUQCSQ6SER.png"},
            {"type": "text", "text": "What are the elements can you see and hear in these medias?"},
        ],
    }
]

# set use audio in video
USE_AUDIO_IN_VIDEO = False

# Preparation for inference
text = processor.apply_chat_template(conversation, add_generation_prompt=True, tokenize=False)
audios, images, videos = process_mm_info(conversation, use_audio_in_video=USE_AUDIO_IN_VIDEO)

/home/is/dwipraseetyo-a/.venv/lib/python3.12/site-packages/qwen_omni_utils/v2_5/audio_process.py:85: UserWarning: PySoundFile failed. Trying audioread instead.
  librosa.load(
/home/is/dwipraseetyo-a/.venv/lib/python3.12/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


NoBackendError: 

In [ ]:
import pandas as pd
import numpy as np
import soundfile as sf
from pathlib import Path
import os
import librosa
import random
import pickle
import pydicom
import requests
import torch
import re
import shutil
from pydicom.datadict import keyword_for_tag
from transformers import AutoProcessor, AutoModelForImageTextToText, BitsAndBytesConfig
from IPython.display import Markdown, display
from openai import OpenAI
from PIL import Image
from tqdm import tqdm
from sklearn.utils import resample
import random
from itertools import combinations

import commons
import const_variable

from huggingface_hub import login
from dotenv import load_dotenv
from datasets import Dataset, concatenate_datasets



def sample_modalities_numeric(df, seed=42):
    df = df.sample(frac=1, random_state=seed).reset_index(drop=True)
    random.seed(seed)
    augmented_rows = []

    # Keep only disease classes 1,2,4
    df = df[df['disease'].isin([1, 2, 4])].reset_index(drop=True)
    disease_classes = df['disease'].unique()

    for label in tqdm(disease_classes, desc="Processing disease classes"):
        class_df = df[df['disease'] == label].reset_index(drop=True)

        # Separate rows by modality presence
        audio_rows = class_df[~class_df['path_file_audio'].isna()]
        image_rows = class_df[~class_df['path_file_image'].isna()]
        symptoms_rows = class_df[~class_df['symptoms_sentence'].isna()]

        # Generate all 7 modality combinations
        combo_to_rows = {combo: [] for combo in [
            ("path_file_audio",),
            ("path_file_image",),
            ("symptoms_sentence",),
            ("path_file_audio", "path_file_image"),
            ("path_file_audio", "symptoms_sentence"),
            ("path_file_image", "symptoms_sentence"),
            ("path_file_audio", "path_file_image", "symptoms_sentence"),
        ]}

        for _, row in class_df.iterrows():
            base_modalities = {
                "path_file_audio": row['path_file_audio'] if pd.notna(row['path_file_audio']) else None,
                "path_file_image": row['path_file_image'] if pd.notna(row['path_file_image']) else None,
                "symptoms_sentence": row['symptoms_sentence'] if pd.notna(row['symptoms_sentence']) else None
            }

            # Create single, double, and triple modality rows
            all_combos = [
                ("path_file_audio",),
                ("path_file_image",),
                ("symptoms_sentence",),
                ("path_file_audio", "path_file_image"),
                ("path_file_audio", "symptoms_sentence"),
                ("path_file_image", "symptoms_sentence"),
                ("path_file_audio", "path_file_image", "symptoms_sentence"),
            ]
            for combo in all_combos:
                new_row = row.to_dict()
                for m in combo:
                    if base_modalities[m] is None:
                        # sample another row with same label that has this modality
                        if m == "path_file_audio" and len(audio_rows) > 0:
                            new_row[m] = audio_rows.sample(
                                1, random_state=seed).iloc[0]['path_file_audio']
                        elif m == "path_file_image" and len(image_rows) > 0:
                            new_row[m] = image_rows.sample(
                                1, random_state=seed).iloc[0]['path_file_image']
                        elif m == "symptoms_sentence" and len(symptoms_rows) > 0:
                            new_row[m] = symptoms_rows.sample(
                                1, random_state=seed).iloc[0]['symptoms_sentence']
                    else:
                        new_row[m] = base_modalities[m]
                new_row["modalities_used"] = combo
                combo_to_rows[combo].append(new_row)

        # Balance: sample same number of rows per combination
        min_count = min(len(rows)
                        for rows in combo_to_rows.values() if len(rows) > 0)
        for combo, rows in combo_to_rows.items():
            if not rows:
                continue
            sampled_rows = random.sample(rows, min_count)
            augmented_rows.extend(sampled_rows)

    # Shuffle final dataset
    final_df = pd.DataFrame(augmented_rows).sample(
        frac=1, random_state=seed).reset_index(drop=True)
    return final_df


random.seed(42)

disease_map = {
    "Others": 0,
    "Tuberculosis": 1,
    "Covid-19": 2
}
disease_map_reverse = {v: k for k, v in disease_map.items()}
prompt_templates = {
    ("audio",): [
        "Based on the cough audio provided,",
        "Evaluate the cough recording carefully,",
        "Consider the characteristics of this cough audio,",
        "From the recorded cough sound,",
        "Assess the features of the cough audio,",
        "Interpret the provided cough recording,",
        "Review the cough audio carefully,",
        "Examine the cough sound,"
    ],
    ("xray",): [
        "Based on the chest x-ray image,",
        "Evaluate the features seen in the x-ray,",
        "Interpret the chest radiograph,",
        "From the provided x-ray scan,",
        "Assess the chest x-ray image,",
        "Review the radiographic scan carefully,",
        "Examine the x-ray image,",
        "Consider the details in this chest x-ray,"
    ],
    ("symptoms",): [
        "Based on the reported symptoms,",
        "Evaluate the patient symptoms,",
        "Interpret the described symptom information,",
        "Review the presented symptoms,",
        "Assess the clinical symptoms carefully,",
        "Examine the provided symptom information,",
        "Consider the described symptoms,",
        "Analyze the symptom details,"
    ],
    ("audio", "xray"): [
        "Based on both the cough audio and chest x-ray,",
        "Evaluate the patient using cough audio and x-ray together,",
        "Interpret the cough recording along with the chest x-ray,",
        "Assess the x-ray and cough audio,",
        "Review the cough sound and chest x-ray together,",
        "Examine both the cough recording and x-ray image,",
        "Consider the x-ray alongside the cough audio,",
        "Analyze the combined cough audio and chest x-ray,"
    ],
    ("audio", "symptoms"): [
        "Based on the cough audio and reported symptoms,",
        "Evaluate the patient using cough audio and symptoms together,",
        "Interpret the cough recording along with the patient symptoms,",
        "Assess the cough sound and symptom description,",
        "Review the combined cough audio and symptoms,",
        "Examine both the cough recording and symptoms,",
        "Consider the cough audio alongside symptom information,",
        "Analyze the cough audio with the reported symptoms,"
    ],
    ("xray", "symptoms"): [
        "Based on the chest x-ray and reported symptoms,",
        "Evaluate the patient using x-ray and symptoms together,",
        "Interpret the chest x-ray along with the patient symptoms,",
        "Assess the x-ray and symptom details,",
        "Review the combined x-ray and symptom information,",
        "Examine both the chest radiograph and symptoms,",
        "Consider the x-ray image alongside the reported symptoms,",
        "Analyze the x-ray together with the symptom description,"
    ],
    ("audio", "xray", "symptoms"): [
        "Based on the cough audio, chest x-ray, and symptoms,",
        "Evaluate the patient using audio, x-ray, and symptoms together,",
        "Interpret the combined cough recording, x-ray, and symptom information,",
        "Assess all inputs: cough audio, x-ray, and symptoms,",
        "Review the cough sound, chest x-ray, and symptom details,",
        "Examine the cough audio, x-ray scan, and patient symptoms,",
        "Consider all data from audio, x-ray, and symptoms,",
        "Analyze the cough recording, x-ray image, and reported symptoms together,"
    ]
}

pseudo_cough_sentences_prefixed = {
    2: ["From this cough sound, the characteristics are dry, persistent, moderate number of coughs, mild hoarseness, intermittent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, hacking, frequent coughs, no hoarseness, persistent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, moderate frequency, mild hoarseness, persistent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, occasional coughs, no hoarseness, intermittent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, persistent, frequent, slight hoarseness, persistent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, hacking, moderate number of coughs, mild hoarseness, persistent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, persistent, few coughs, no hoarseness, intermittent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, persistent, moderate frequency, mild hoarseness, persistent pattern; this indicates COVID-19."],
    1: ["From this cough sound, the characteristics are wet, persistent, moderate number of coughs, mild hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, hacking, frequent coughs, mild hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, persistent, many coughs, moderate hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, hacking, few coughs, mild hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, persistent, moderate frequency, moderate hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, hacking, frequent coughs, mild hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, persistent, many coughs, moderate hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, hacking, moderate number of coughs, mild hoarseness, persistent pattern; this indicates TB."],
    0: ["From this cough sound, the characteristics are occasional, mild, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are rare, mild, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are occasional, non-productive, mild hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are intermittent, mild, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are rare, non-specific, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are mild, occasional, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are intermittent, non-productive, mild hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are occasional, mild, no hoarseness, intermittent pattern; this cannot determine a specific disease."]
}
modalities_combinations = [
    ("path_file_audio",),
    ("path_file_image",),
    ("symptoms_sentence",),
    ("path_file_audio", "path_file_image"),
    ("path_file_audio", "symptoms_sentence"),
    ("path_file_image", "symptoms_sentence"),
    ("path_file_audio", "path_file_image", "symptoms_sentence"),
]

mod_map = {
    "path_file_audio": "audio",
    "path_file_image": "xray",
    "symptoms_sentence": "symptoms"
}


def map_modalities(row):
    return tuple(mod_map[m] for m in row if m in mod_map)


DATA_PATH = "/home/is/dwipraseetyo-a/NAS_HAI/Datasets"
DESTINATION_PATH = "/home/is/dwipraseetyo-a/NAS_HAI/Datasets/grpo_3modalities_datasets"

system_prompt = '''You are an advanced medical assistant AI specialized in analyzing and diagnosing clinical conditions, capable of perceiving auditory and visual inputs.
You can interpret and reason over various medical inputs, including auditory inputs, visual inputs, and patient symptoms, individually or in combination, depending on what is provided.
Your task is to analyze the given input, explain your reasoning, and give a possible diagnosis.
Always respond in the following format:
<think>{Analyze the available data: X-ray findings if present, cough audio characteristics if provided, and reported symptoms to determine the most likely disease.}</think>
<answer>{Determine the disease}</answer>'''

for split in ['val']:
    df1 = pd.read_csv(f"{DATA_PATH}/coda/metadata_llm.csv.{split}").rename(columns={
        "participant": "user_id", "tb_status": "disease", "path_file": "path_file_audio"})
    df1 = df1[['user_id', 'disease', 'path_file_audio',
               'symptoms_sentence', 'llm_analyze_symptoms']]
    df1["disease"] = df1["disease"].replace(0, 4)
    df1 = df1.groupby("user_id", group_keys=False).apply(
        lambda x: x.sample(n=min(len(x), 70), random_state=42)
    )
    df2 = pd.read_csv(f"{DATA_PATH}/ukcovid/metadata_llm.csv.{split}").rename(
        columns={"participant_identifier": "user_id", "covid_test_result": "disease"})
    df2["disease"] = df2["disease"].replace(1, 2)
    df2["disease"] = df2["disease"].replace(0, 4)
    df2 = df2[['user_id', 'disease', 'path_file_audio',
               'symptoms_sentence', 'llm_analyze_symptoms']]
    df3 = pd.read_csv(f"{DATA_PATH}/xray_metadata_llm_final.csv.{split}").rename(columns={
        "path_file": "path_file_image", "formatted_llm_analyze_image": "llm_analyze_image"})
    df_combined = pd.concat([df1, df2, df3], axis=0, ignore_index=True)

    if split == "val":
        split = "validation"
    df_aug = sample_modalities_numeric(df_combined)
    min_count = df_aug.groupby(['disease', 'modalities_used']).size().min()
    df_balanced = (
        df_aug
        .groupby(['disease', 'modalities_used'], group_keys=False)
        .apply(lambda x: resample(x, replace=False, n_samples=min_count, random_state=42))
    )
    df_balanced['disease'] = df_balanced['disease'].replace({4: 0})
    df_balanced['path_file_audio'] = df_balanced['path_file_audio'].apply(
        lambda x: f"{split}/{x.split('/')[-1]}" if pd.notna(x) else x)

    df_balanced['path_file_image'] = df_balanced['path_file_image'].apply(
        lambda x: f"{split}/{x.split('/')[-1]}" if pd.notna(x) else x)
    df_balanced.reset_index(drop=True, inplace=True)
    df_balanced['modalities_simple'] = df_balanced['modalities_used'].apply(map_modalities)
    df_balanced.drop(['modalities_used'], axis=1, inplace=True)
    break

/tmp/ipykernel_3397339/1852000919.py:266: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  df1 = df1.groupby("user_id", group_keys=False).apply(
Processing disease classes: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:19<00:00,  6.33s/it]
/tmp/ipykernel_3397339/1852000919.py:286: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(lambda x: r

In [16]:
# Columns to check for duplicates


# Total number of rows
total_rows = len(df_balanced)

# Number of duplicated rows (first occurrence is not counted as duplicate)
num_duplicates = df_balanced.duplicated(subset=key_cols, keep='first').sum()

# Duplication percentage
dup_percentage = num_duplicates / total_rows * 100

print(f"Total rows: {total_rows}")
print(f"Duplicated rows: {num_duplicates}")
print(f"Duplication percentage: {dup_percentage:.2f}%")

Total rows: 16653
Duplicated rows: 4835
Duplication percentage: 29.03%


In [ ]:
upper_limit = 793  # from your observed max




print(df_balanced_nodup.groupby(['disease','modalities_simple']).size())

disease  modalities_simple      
0        (audio,)                   793
         (audio, symptoms)          793
         (audio, xray)              793
         (audio, xray, symptoms)    793
         (symptoms,)                793
         (xray,)                    793
         (xray, symptoms)           793
1        (audio,)                   793
         (audio, symptoms)          793
         (audio, xray)              793
         (audio, xray, symptoms)    793
         (symptoms,)                793
         (xray,)                    793
         (xray, symptoms)           793
2        (audio,)                   793
         (audio, symptoms)          793
         (audio, xray)              793
         (audio, xray, symptoms)    793
         (symptoms,)                793
         (xray,)                    793
         (xray, symptoms)           793
dtype: int64


/tmp/ipykernel_3397339/3284435311.py:17: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(drop_dups_with_cap)


In [11]:
# Columns to check for duplicates
key_cols = ["disease", "path_file_audio", "path_file_image", "symptoms_sentence"]

# Total number of rows
total_rows = len(df_balanced_nodup)

# Number of duplicated rows (first occurrence is not counted as duplicate)
num_duplicates = df_balanced_nodup.duplicated(subset=key_cols, keep='first').sum()

# Duplication percentage
dup_percentage = num_duplicates / total_rows * 100

print(f"Total rows: {total_rows}")
print(f"Duplicated rows: {num_duplicates}")
print(f"Duplication percentage: {dup_percentage:.2f}%")

Total rows: 16653
Duplicated rows: 4835
Duplication percentage: 29.03%


In [7]:
df_balanced_nodup['disease'].value_counts()

disease
0    4874
2    4481
1    2463
Name: count, dtype: int64

np.int64(793)

In [ ]:
You are an advanced medical assistant AI specialized in analyzing and diagnosing clinical conditions. 
You can interpret and reason over various medical inputs, including auditory inputs, visual inputs, and patient symptoms, individually or in combination, depending on what is provided. 

Your task is to:
1. Analyze the given input (X-ray findings if present, cough audio characteristics if provided, and reported symptoms if provided).  
2. Explain your reasoning step by step.  
3. Give the most likely diagnosis.  

Always respond in the following structured format:

<think>
Analyze the available data, explain your reasoning, and show how you arrived at your conclusion.
</think>

<answer>
State the most likely disease or diagnosis.
</answer>

In [7]:
instruct_array

[{'messages': [{'role': 'system',
    'content': [{'type': 'text',
      'text': 'You are an advanced medical assistant AI specialized in analyzing and diagnosing clinical conditions, capable of perceiving auditory and visual inputs.\nYou can interpret and reason over various medical inputs, including auditory inputs, visual inputs, and patient symptoms, individually or in combination, depending on what is provided.\nYour task is to analyze the given input, explain your reasoning, and give a possible diagnosis.\nAlways respond in the following format:\n<think>{Analyze the available data: X-ray findings if present, cough audio characteristics if provided, and reported symptoms to determine the most likely disease.}</think>\n<answer>{Determine the disease}</answer>'}]},
   {'role': 'user',
    'content': [{'type': 'text',
      'text': "<audio><image>Evaluate the cough recording carefully,, Determine what disease this could indicate, or answer 'Others' if you cannot determine."},
     {'

In [125]:
    for idx, row in df_balanced.iterrows():
        key = row['modalities_simple']
        if key in prompt_templates:
            prompt = prompt_templates[key]

        break

In [128]:
prompt

['Based on the provided cough audio',
 'Listen to this cough sound',
 'Does the cough audio indicate',
 'Analyze the following cough sound']

In [124]:
df_balanced.groupby(['disease','modalities_simple']).size()

disease  modalities_simple      
0        (audio,)                   13081
         (audio, symptoms)          13081
         (audio, xray)              13081
         (audio, xray, symptoms)    13081
         (symptoms,)                13081
         (xray,)                    13081
         (xray, symptoms)           13081
1        (audio,)                   13081
         (audio, symptoms)          13081
         (audio, xray)              13081
         (audio, xray, symptoms)    13081
         (symptoms,)                13081
         (xray,)                    13081
         (xray, symptoms)           13081
2        (audio,)                   13081
         (audio, symptoms)          13081
         (audio, xray)              13081
         (audio, xray, symptoms)    13081
         (symptoms,)                13081
         (xray,)                    13081
         (xray, symptoms)           13081
dtype: int64

In [122]:
df_balanced

user_id  disease  \
0       C8ECQ5K95NWZ        1   
1       CODA_TB_0954        1   
2       CODA_TB_0328        1   
3       CODA_TB_0719        1   
4       CODA_TB_0776        1   
...              ...      ...   
274696      P0020844        0   
274697      P0039755        0   
274698      P0031024        0   
274699      P0021648        0   
274700  ILQ2ZVZDX5RM        0   

                                          path_file_audio  \
0                            train/l_CODA_TB_0571_523.wav   
1                             train/l_CODA_TB_0954_89.wav   
2                            train/l_CODA_TB_0328_120.wav   
3                             train/l_CODA_TB_0719_28.wav   
4                             train/l_CODA_TB_0776_11.wav   
...                                                   ...   
274696                   train/44286_jsxAcQbsbmXd63aN.wav   
274697                   train/25376_pVeuJv9aGJypbjbt.wav   
274698  train/71-14-c465ce33-95e3-42a6-855cee183004085...   
274699                   train/13115_1gEa9mH12gtrxFPX.wav   
274700                                                NaN   

                                        symptoms_sentence  \
0                                                     NaN   
1       hiv status is Negative, night sweats is Yes, w...   
2       age is 52, height is 172.5, gender is Male, we...   
3       age is 61, hiv status is Negative, height is 1...   
4       weight is 55.8, weight loss is Yes, height is ...   
...                                                   ...   
274696  loss of taste is no, runny or blocked nose is ...   
274697  gender is Male, cough any is no, sore throat i...   
274698  new continuous cough is no, fatigue is no, cha...   
274699  diarrhoea is no, new continuous cough is no, s...   
274700  loss of taste is no, cough any is no, new cont...   

                                     llm_analyze_symptoms  \
0                                                     NaN   
1       Based on the symptoms provided, the patient is...   
2       Based on the symptoms provided, the patient is...   
3       Based on the provided symptoms, the patient is...   
4       The patient's symptoms of night sweats and wei...   
...                                                   ...   
274696  Based on the symptoms provided, the patient is...   
274697  Based on the symptoms provided, the patient is...   
274698  Based on the symptoms provided, the patient is...   
274699  Based on the symptoms provided, the patient is...   
274700                                                NaN   

               path_file_image  \
0       train/C8ECQ5K95NWZ.png   
1                          NaN   
2                          NaN   
3                          NaN   
4                          NaN   
...                        ...   
274696                     NaN   
274697                     NaN   
274698                     NaN   
274699                     NaN   
274700  train/ILQ2ZVZDX5RM.jpg   

                                        llm_analyze_image modalities_simple  
0       The chest X-ray findings are highly suggestive...          (audio,)  
1                                                     NaN          (audio,)  
2                                                     NaN          (audio,)  
3                                                     NaN          (audio,)  
4                                                     NaN          (audio,)  
...                                                   ...               ...  
274696                                                NaN       (symptoms,)  
274697                                                NaN       (symptoms,)  
274698                                                NaN       (symptoms,)  
274699                                                NaN       (symptoms,)  
274700  The heart size appears within normal limits. T...       (symptoms,)  

[274701 rows x 8 columns]

In [111]:
# Columns to check for duplicates
key_cols = ["disease", "path_file_audio", "path_file_image", "symptoms_sentence"]

# Total number of rows
total_rows = len(df_balanced)

# Number of duplicated rows (first occurrence is not counted as duplicate)
num_duplicates = df_balanced.duplicated(subset=key_cols, keep='first').sum()

# Duplication percentage
dup_percentage = num_duplicates / total_rows * 100

print(f"Total rows: {total_rows}")
print(f"Duplicated rows: {num_duplicates}")
print(f"Duplication percentage: {dup_percentage:.2f}%")

Total rows: 274701
Duplicated rows: 132595
Duplication percentage: 48.27%


In [99]:
df_balanced

user_id  disease  \
16113   C8ECQ5K95NWZ        1   
377367  CODA_TB_0954        1   
221311  CODA_TB_0328        1   
291196  CODA_TB_0719        1   
150228  CODA_TB_0776        1   
...              ...      ...   
282241      P0020844        4   
475879      P0039755        4   
373239      P0031024        4   
152256      P0021648        4   
240174  ILQ2ZVZDX5RM        4   

                                          path_file_audio  \
16113   /home/is/dwipraseetyo-a/NAS_HAI/Datasets/coda/...   
377367  /home/is/dwipraseetyo-a/NAS_HAI/Datasets/coda/...   
221311  /home/is/dwipraseetyo-a/NAS_HAI/Datasets/coda/...   
291196  /home/is/dwipraseetyo-a/NAS_HAI/Datasets/coda/...   
150228  /home/is/dwipraseetyo-a/NAS_HAI/Datasets/coda/...   
...                                                   ...   
282241  /home/is/dwipraseetyo-a/NAS_HAI/Datasets/ukcov...   
475879  /home/is/dwipraseetyo-a/NAS_HAI/Datasets/ukcov...   
373239  /home/is/dwipraseetyo-a/NAS_HAI/Datasets/ukcov...   
152256  /home/is/dwipraseetyo-a/NAS_HAI/Datasets/ukcov...   
240174                                                NaN   

                                        symptoms_sentence  \
16113                                                 NaN   
377367  hiv status is Negative, night sweats is Yes, w...   
221311  age is 52, height is 172.5, gender is Male, we...   
291196  age is 61, hiv status is Negative, height is 1...   
150228  weight is 55.8, weight loss is Yes, height is ...   
...                                                   ...   
282241  loss of taste is no, runny or blocked nose is ...   
475879  gender is Male, cough any is no, sore throat i...   
373239  new continuous cough is no, fatigue is no, cha...   
152256  diarrhoea is no, new continuous cough is no, s...   
240174  loss of taste is no, cough any is no, new cont...   

                                     llm_analyze_symptoms  \
16113                                                 NaN   
377367  Based on the symptoms provided, the patient is...   
221311  Based on the symptoms provided, the patient is...   
291196  Based on the provided symptoms, the patient is...   
150228  The patient's symptoms of night sweats and wei...   
...                                                   ...   
282241  Based on the symptoms provided, the patient is...   
475879  Based on the symptoms provided, the patient is...   
373239  Based on the symptoms provided, the patient is...   
152256  Based on the symptoms provided, the patient is...   
240174                                                NaN   

                                          path_file_image  \
16113   /home/is/dwipraseetyo-a/NAS_HAI/Datasets/combi...   
377367                                                NaN   
221311                                                NaN   
291196                                                NaN   
150228                                                NaN   
...                                                   ...   
282241                                                NaN   
475879                                                NaN   
373239                                                NaN   
152256                                                NaN   
240174  /home/is/dwipraseetyo-a/NAS_HAI/Datasets/combi...   

                                        llm_analyze_image  \
16113   The chest X-ray findings are highly suggestive...   
377367                                                NaN   
221311                                                NaN   
291196                                                NaN   
150228                                                NaN   
...                                                   ...   
282241                                                NaN   
475879                                                NaN   
373239                                                NaN   
152256                                                NaN   
240174  The h

In [1]:
import numpy as np
import pandas as pd


df1 = pd.read_csv("/home/is/dwipraseetyo-a/NAS_HAI/Datasets/grpo_3modalities_datasets/train.csv")
df2 = pd.read_csv("/home/is/dwipraseetyo-a/NAS_HAI/Datasets/grpo_3modalities_datasets/validation.csv")

In [2]:
df1

messages  \
0      [{'role': 'system', 'content': [{'type': 'text...   
1      [{'role': 'system', 'content': [{'type': 'text...   
2      [{'role': 'system', 'content': [{'type': 'text...   
3      [{'role': 'system', 'content': [{'type': 'text...   
4      [{'role': 'system', 'content': [{'type': 'text...   
...                                                  ...   
99813  [{'role': 'system', 'content': [{'type': 'text...   
99814  [{'role': 'system', 'content': [{'type': 'text...   
99815  [{'role': 'system', 'content': [{'type': 'text...   
99816  [{'role': 'system', 'content': [{'type': 'text...   
99817  [{'role': 'system', 'content': [{'type': 'text...   

                   audio_file_name  \
0       train/l_CODA_TB_0002_2.wav   
1       train/l_CODA_TB_0002_1.wav   
2      train/l_CODA_TB_0003_25.wav   
3      train/l_CODA_TB_0003_14.wav   
4       train/l_CODA_TB_0003_9.wav   
...                            ...   
99813                    train/nan   
99814                    train/nan   
99815                    train/nan   
99816                    train/nan   
99817                    train/nan   

                                                solution    identifier  \
0      <think>Okay, let's see. Based on the patient's...  CODA_TB_0002   
1      <think>Okay, let's see. Based on the patient's...  CODA_TB_0002   
2      <think>Okay, let's see. Based on the provided ...  CODA_TB_0003   
3      <think>Okay, let's see. Based on the provided ...  CODA_TB_0003   
4      <think>Okay, let's see. Based on the provided ...  CODA_TB_0003   
...                                                  ...           ...   
99813  <think>Okay, let's see. The chest X-ray findin...  1GOVQY01H4M3   
99814  <think>Okay, let's see. The chest X-ray findin...  RZY9JRW4JK4R   
99815  <think>Okay, let's see. The chest X-ray findin...  BKZ6GYHYEV2Y   
99816  <think>Okay, let's see. The chest X-ray findin...  0BTN61W0Y4LY   
99817  <think>Okay, let's see. The chest X-ray findin...  ERSM47EVFOOD   

              image_file_name  
0                   train/nan  
1                   train/nan  
2                   train/nan  
3                   train/nan  
4                   train/nan  
...                       ...  
99813  train/1GOVQY01H4M3.png  
99814  train/RZY9JRW4JK4R.png  
99815  train/BKZ6GYHYEV2Y.png  
99816  train/0BTN61W0Y4LY.png  
99817  train/ERSM47EVFOOD.png  

[99818 rows x 5 columns]

In [31]:
df1['audio_file_name'].value_counts()

audio_file_name
train/nan                                              35474
train/15185_l20RlIItScPYhUvN.wav                           1
train/30333_3D5YOqGXrKaJ56cv.wav                           1
train/13782_j4KY3o7o7im3sVjv.wav                           1
train/71-13-1df528cc-462a-4639-87a864108b539a2b.wav        1
train/8041_AQOeCJXnYV8kfj20.wav                            1
train/10212_qyBHnWpsAkcTgCHI.wav                           1
train/18248_HncmHEDtM1QHrVkP.wav                           1
train/20859_jQRKkn1sblODSpJQ.wav                           1
train/62-13-3fa555a8-30a2-4694-a70be291040e9ab8.wav        1
train/47084_Ctbn7PQfZcfVxdPu.wav                           1
train/71-13-9cd57d5a-3b24-4c5a-80fe842afb442658.wav        1
train/28904_OFnvEaUZ07HsuErb.wav                           1
train/4566_kQotNYV6rDmErhY8.wav                            1
train/71-13-dc749018-e535-4996-a0910047919e6ce5.wav        1
train/26516_jVYX345HoZLHHSsv.wav                           1
train/38

In [9]:
len(df1)

99818

In [16]:
35474 / (99818)

0.3553868039832495

In [17]:
1 - 0.355

0.645

In [12]:
35474 / (99818 + 35474)

0.26220323448540933

In [28]:
1829 + 1829 + 1254

4912

In [29]:
99818 / 4912

20.321254071661237

In [15]:
(99818 - 35474) / (99818 + 35474)

0.47559353102918134

In [27]:
99818 - 35474

64344

In [ ]:
%cd /home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni
%pwd

import os
os.environ["CUDA_VISIBLE_DEVICES"] = "1"
print("CUDA_VISIBLE_DEVICES:", os.environ["CUDA_VISIBLE_DEVICES"])

import torch
device_name = torch.cuda.get_device_name(0)
for i in range(torch.cuda.device_count()):
    props = torch.cuda.get_device_properties(i)
    print(f"Logical index: {i}, Name: {props.name}")

/home/ldap-users-2/dwipraseetyo-a/Project/Qwen2.5-Omni
CUDA_VISIBLE_DEVICES: 0
Logical index: 0, Name: NVIDIA GeForce RTX 3090


In [3]:
import commons
import const_variable
from my_datasets import QwenOmniFinetuneDataset

In [ ]:
import torch, re
from collections import Counter
from transformers import AutoTokenizer, AutoModelForCausalLM, GenerationConfig

# model/tokenizer bootstrap
tok = AutoTokenizer.from_pretrained("your/policy")
mdl = AutoModelForCausalLM.from_pretrained("your/policy").eval().to("cuda")

COT_PROMPT = """Solve the problem step by step. Show reasoning, then a short result inside <final>...</final>.
Question: {q}

Reasoning:
"""

def gen_candidates(prompt, k=8, strategy="beam"):
    if strategy == "beam":
        gen_cfg = GenerationConfig(
            num_beams=k, num_return_sequences=k, do_sample=False,
            max_new_tokens=256, early_stopping=True,
            return_dict_in_generate=True, output_scores=True
        )
    else:  # sampling
        gen_cfg = GenerationConfig(
            do_sample=True, top_p=0.9, temperature=0.7,
            num_return_sequences=k, max_new_tokens=256,
            return_dict_in_generate=True, output_scores=True
        )
    out = mdl.generate(**tok(prompt, return_tensors="pt").to(mdl.device),
                       generation_config=gen_cfg)
    texts = tok.batch_decode(out.sequences, skip_special_tokens=True)
    scores = out.sequences_scores  # higher = more likely
    return texts, scores

def extract_final(text):
    m = re.search(r"<final>(.*?)</final>", text, flags=re.S)
    return m.group(1).strip() if m else None

@torch.no_grad()
def answer_logprob(prompt_prefix, answer):
    # score only the answer tokens conditioned on the prefix
    ctx_ids = tok(prompt_prefix, return_tensors="pt").to(mdl.device).input_ids
    ans_ids = tok(answer, return_tensors="pt").to(mdl.device).input_ids
    full_ids = torch.cat([ctx_ids, ans_ids], dim=1)
    labels = full_ids.clone()
    labels[:, :ctx_ids.size(1)] = -100
    out = mdl(input_ids=full_ids, labels=labels)
    n_tokens = (labels != -100).sum().item()
    return -(out.loss.item() * n_tokens)  # sum logprob

def cot_high_confidence(question, k=8, strategy="beam"):
    prompt = COT_PROMPT.format(q=question)
    texts, seq_scores = gen_candidates(prompt, k=k, strategy=strategy)
    # Option A: pick by full-sequence likelihood
    best_idx = int(torch.argmax(seq_scores))
    best_full = texts[best_idx]
    # Option B (recommended): pick by answer-only likelihood
    ans_scores = []
    for t in texts:
        ans = extract_final(t)
        if ans is None: ans_scores.append(float("-inf")); continue
        prefix = t.split("<final>")[0] + "<final>"
        ans_scores.append(answer_logprob(prefix, ans))
    best_idx_ans = int(torch.tensor(ans_scores).argmax())
    return {
        "selected": extract_final(texts[best_idx_ans]),
        "rationale": texts[best_idx_ans],
        "answer_logprob": ans_scores[best_idx_ans],
        "fallback_fullseq_idx": best_idx
    }

def self_consistency(question, k=20):
    prompt = COT_PROMPT.format(q=question)
    texts, _ = gen_candidates(prompt, k=k, strategy="sample")
    finals = [extract_final(t) for t in texts]
    finals = [f for f in finals if f is not None]
    if not finals: return {"selected": None, "votes": {}, "rationales": []}
    votes = Counter(finals)
    winner, win_count = votes.most_common(1)[0]
    # tie-break with answer logprob
    ties = [a for a,cnt in votes.items() if cnt == win_count]
    if len(ties) > 1:
        scored = []
        for t in texts:
            a = extract_final(t)
            if a in ties:
                prefix = t.split("<final>")[0] + "<final>"
                scored.append((a, answer_logprob(prefix, a), t))
        scored.sort(key=lambda x: x[1], reverse=True)
        winner = scored[0][0]
        best_rationale = scored[0][2]
    else:
        best_rationale = next(t for t in texts if extract_final(t) == winner)
    return {
        "selected": winner,
        "votes": dict(votes),
        "rationale": best_rationale
    }

# Works for SFT and RL-trained policies. If you have a reward model, replace answer_logprob(...) with reward scoring for rerank.

# Keep outputs parseable. The <final>...</final> contract is the control plane.

# For latency, cut k or run batch scoring on GPU.

# For guardrails, add no_repeat_ngram_size, repetition_penalty, and bad_words_ids if needed.

In [18]:
halo = [[{'role': 'system', 'content': [{'type': 'text', 'text': '\nYou are an advanced medical assistant AI specialized in analyzing and diagnosing clinical conditions, capable of perceiving auditory and visual inputs. \nYou can interpret and reason over various medical inputs, including auditory inputs, visual inputs, and patient symptoms, individually or in combination, depending on what is provided. \nYour task is to analyze the given input, explain your reasoning, and give a possible diagnosis. Answer are enclosed within <answer> </answer> tags, respectively, i.e., <answer> answer here </answer> .\nAlways respond in the following format:\n\n## ⚠️ Points to Review and Disclaimer\n<If no auditory or visual input is provided>\n\n## 🧠 Overview\n<answer> <Positive or Negative Diagnosis> </answer>\n\n## 📋 Observations\n**Chest X-ray:**\n<Your explanation based on the relevant visual input>"\n\n**Symptoms:**\n<Your explanation based on the input symptoms>"\n\n**Audio:**\n<Your explanation based on the input audio>"\n'}]}, {'role': 'user', 'content': [{'type': 'text', 'text': '. Listen to this cough sound, is it Positive Tuberculosis or Negative Tuberculosis?. '}, {'type': 'audio', 'audio': '/home/is/dwipraseetyo-a/NAS_HAI/Datasets/cidrz/wavs/03-399-0329_2.wav', 'audio_start': 0.1, 'audio_end': 3.1}]}], [{'role': 'system', 'content': [{'type': 'text', 'text': '\nYou are an advanced medical assistant AI specialized in analyzing and diagnosing clinical conditions, capable of perceiving auditory and visual inputs. \nYou can interpret and reason over various medical inputs, including auditory inputs, visual inputs, and patient symptoms, individually or in combination, depending on what is provided. \nYour task is to analyze the given input, explain your reasoning, and give a possible diagnosis. Answer are enclosed within <answer> </answer> tags, respectively, i.e., <answer> answer here </answer> .\nAlways respond in the following format:\n\n## ⚠️ Points to Review and Disclaimer\n<If no auditory or visual input is provided>\n\n## 🧠 Overview\n<answer> <Positive or Negative Diagnosis> </answer>\n\n## 📋 Observations\n**Chest X-ray:**\n<Your explanation based on the relevant visual input>"\n\n**Symptoms:**\n<Your explanation based on the input symptoms>"\n\n**Audio:**\n<Your explanation based on the input audio>"\n'}]}, {'role': 'user', 'content': [{'type': 'text', 'text': '. Based on the provided cough audio, is this case Positive Tuberculosis or Negative Tuberculosis?. '}, {'type': 'audio', 'audio': '/home/is/dwipraseetyo-a/NAS_HAI/Datasets/cidrz/wavs/01-399-0987_3.wav', 'audio_start': 2.0, 'audio_end': 5.0}]}]]

In [19]:
halo[0]

[{'role': 'system',
  'content': [{'type': 'text',
    'text': '\nYou are an advanced medical assistant AI specialized in analyzing and diagnosing clinical conditions, capable of perceiving auditory and visual inputs. \nYou can interpret and reason over various medical inputs, including auditory inputs, visual inputs, and patient symptoms, individually or in combination, depending on what is provided. \nYour task is to analyze the given input, explain your reasoning, and give a possible diagnosis. Answer are enclosed within <answer> </answer> tags, respectively, i.e., <answer> answer here </answer> .\nAlways respond in the following format:\n\n## ⚠️ Points to Review and Disclaimer\n<If no auditory or visual input is provided>\n\n## 🧠 Overview\n<answer> <Positive or Negative Diagnosis> </answer>\n\n## 📋 Observations\n**Chest X-ray:**\n<Your explanation based on the relevant visual input>"\n\n**Symptoms:**\n<Your explanation based on the input symptoms>"\n\n**Audio:**\n<Your explanation 

In [4]:
list(const_variable.prompt_templates.keys())

[('audio',),
 ('xray',),
 ('symptoms',),
 ('audio', 'xray'),
 ('audio', 'symptoms'),
 ('xray', 'symptoms'),
 ('audio', 'xray', 'symptoms')]

In [56]:
files

['/home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni/outputs/qwen25omni3b-think-balance-grspo-tokenintext-250880-trainall/v3-20250815-144305/aresults_501760_1.0.txt',
 '/home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni/outputs/qwen25omni3b-think-balance-grspo-tokenintext-250880-trainall/v3-20250815-144305/aresults_501760_0.0.txt',
 '/home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni/outputs/qwen25omni3b-think-balance-grspo-tokenintext-250880-trainall/v3-20250815-144305/aresults_501760_0.5.txt']

In [26]:
import re
import ast
import glob
import pandas as pd

# Show full table
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)
pd.set_option('display.width', None)

loaded_file = "/home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni/outputs/qwen25omni3b-reason-notallpresent-trl-sft-balance"
files = glob.glob(f"{loaded_file}/results_*.txt")

pattern = re.compile(
    r"Modalities:\s*(\(.+?\))\s*"
    r"Accuracy:\s*([\d.]+)\s*"
    r"Sensitivity:\s*([\d.]+)\s*"
    r"Specificity:\s*([\d.]+)",
    re.MULTILINE | re.DOTALL
)

all_data = []
for file in files:
    temp = float(file.split("_")[-1].replace(".txt", ""))
    with open(file, "r") as f:
        text = f.read()
    for match in pattern.finditer(text):
        modalities = ast.literal_eval(match.group(1))
        # Convert tuple to readable string
        mod_str = " + ".join(modalities).title().replace("Symptoms", "Symp")
        acc = float(match.group(2))
        sens = float(match.group(3))
        spec = float(match.group(4))
        #youden = sens + spec - 1
        #all_data.append([temp, mod_str, acc, youden])
        all_data.append([temp, mod_str, acc, sens, spec])

df = pd.DataFrame(all_data, columns=["Temperature", "Modalities", "Accuracy", "sens", "spec"])
df_agg = df.groupby(["Temperature", "Modalities"], as_index=False).mean()
pivot_df = df_agg.pivot(index="Temperature", columns="Modalities", values=["Accuracy", "sens", "spec"])
pivot_df = pivot_df.swaplevel(axis=1).sort_index(axis=1, level=0).reset_index()
modalities_order = ["Audio", "Xray", "Symp", "Audio + Xray", "Audio + Symp", "Xray + Symp", "Audio + Xray + Symp"]

pivot_df.columns = pd.MultiIndex.from_tuples(pivot_df.columns)
cols = [("Temperature", "")]  
for m in modalities_order:
    for metric in ["Accuracy", "sens", "spec"]:
        if (m, metric) in pivot_df.columns:
            cols.append((m, metric))

pivot_df = pivot_df[cols]
# Exclude the 'Temperature' column from numeric aggregation
numeric_cols = pivot_df.columns[pd.Index([c[1] for c in pivot_df.columns]) != ""]

# Compute mean across all temperatures
agg_mean = pivot_df[numeric_cols].mean().to_frame().T

# Add a placeholder for 'Temperature' to indicate it's an aggregate
agg_mean[("Temperature", "")] = "Mean"

# Reorder columns to match original pivot_df order
agg_mean = agg_mean[pivot_df.columns]

# Append aggregate row to pivot_df
pivot_df_with_mean = pd.concat([pivot_df, agg_mean], ignore_index=True)

pivot_df_with_mean


Temperature     Audio                     Xray                     Symp  \
               Accuracy sens      spec  Accuracy sens      spec  Accuracy   
0         0.0  0.805600  0.0  0.977500  0.838200  0.0  0.962000  0.871300   
1         0.5  0.814800  0.0  0.988800  0.849300  0.0  0.974700  0.864000   
2         1.0  0.824100  0.0  1.000000  0.841900  0.0  0.966200  0.867600   
3        Mean  0.814833  0.0  0.988767  0.843133  0.0  0.967633  0.867633   

                    Audio + Xray                     Audio + Symp            \
       sens    spec     Accuracy      sens      spec     Accuracy      sens   
0  0.028600  0.9958     0.805600  0.052600  0.966300     0.824100  0.000000   
1  0.000000  0.9916     0.824100  0.000000  1.000000     0.814800  0.000000   
2  0.000000  0.9958     0.814800  0.000000  0.988800     0.833300  0.052600   
3  0.009533  0.9944     0.814833  0.017533  0.985033     0.824067  0.017533   

            Xray + Symp              Audio + Xray + Symp            
       spec    Accuracy sens    spec            Accuracy sens spec  
0  1.000000      0.8676  0.0  0.9958              0.8241  0.0  1.0  
1  0.988800      0.8676  0.0  0.9958              0.8241  0.0  1.0  
2  1.000000      0.8676  0.0  0.9958              0.8241  0.0  1.0  
3  0.996267      0.8676  0.0  0.9958              0.8241  0.0  1.0

In [ ]:
import pickle, os, re, random
from PIL import Image
from tqdm import tqdm
import numpy as np
import pandas as pd

import torch
from torch.utils.data import DataLoader
from qwen_omni_utils import process_mm_info
from my_qwenwrapper import get_OmniModel, get_stoppingcrit
from datasets import Dataset
from swift.llm import PtEngine, RequestConfig, InferRequest
from sklearn.metrics import accuracy_score, confusion_matrix
import matplotlib.pyplot as plt
import seaborn as sns

import commons
import const_variable
from my_datasets import QwenOmniFinetuneDataset

import warnings
warnings.simplefilter(action="ignore", category=FutureWarning)

def get_labelAnswer(text):
    sol_match = re.search(r'<answer>(.*?)</answer>', text, flags=re.IGNORECASE)
    answer = sol_match.group(1).strip() if sol_match else text.strip()
    label = 1 if answer == "Positive Tuberculosis" else 0
    return label

os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"
os.environ['MAX_PIXELS'] = '250880'
DATA_PATH = "/home/is/dwipraseetyo-a/NAS_HAI/Datasets/cidrz"

model = "Qwen/Qwen2.5-Omni-3B"
Checkpoint_PATH = "outputs/qwen25omni3b-think-balance-grspo-tokenintext-250880-trainall/v3-20250815-144305"
Checkpoint_Number = "checkpoint-485"

system_prompt = (
    "A conversation between User and Advanced medical assistant specialized in analyzing and diagnosing clinical conditions. and the Assistant determines whether the case is Positive or Negative. The assistant "
    "first thinks about the reasoning process in the mind and then provides the user with the answer. The reasoning "
    "process and answer are enclosed within <think> </think> and <answer> </answer> tags, respectively, i.e., "
    "<think> reasoning process here </think><answer> answer here </answer>"
)

random.seed(42)
df = pd.read_csv(f"{DATA_PATH}/metadata_cut_processed.csv.test")
df_llm_symptoms = ( pd.read_csv(f"datas/reasoning/symptoms/gpt-4o-mini_symptoms.csv.test").groupby('barcode', group_keys=False).apply(lambda x: x.sample(1), include_groups=True).reset_index(drop=True) ) 
df_llm_images = ( pd.read_csv(f"datas/reasoning/xray/medgemma_xray_formatted.csv.test").groupby('path_file_image', group_keys=False).apply(lambda x: x.sample(1), include_groups=True).reset_index(drop=True) )
df = pd.merge(df, df_llm_symptoms, on='barcode', how='left')
df = pd.merge(df, df_llm_images, on='path_file_image', how='left')
df = df.rename(columns={'coughdur': 'cough_duration', 'ngtsweats': 'night_sweets', 'weightloss': 'weight_loss', 'body_wt': 'body_weight'})

for modalities in list(const_variable.prompt_templates.keys()):
    instruct_array_test = []
    for now_row in tqdm(df.itertuples(), desc=f"Processing Datasets", total=len(df)):
        row_dict = now_row._asdict()
        now_audiopath = "/home/is/dwipraseetyo-a/NAS_HAI/Datasets/cidrz/" +  now_row.path_file_audio
        now_imgaepath = "/home/is/dwipraseetyo-a/NAS_HAI/Datasets/cidrz/" +  now_row.path_file_image

        #modalities = ["audio", "xray", "symptoms"]
        key = modalities #tuple(modalities)
        if key in const_variable.prompt_templates:
            last_sentence_question = random.choice(const_variable.prompt_templates[key]) + ". "
        answer = commons.generate_tb_response(modalities, now_row.llm_analyze_symptoms, now_row.llm_analyze_image, positive=(now_row.ground_truth_tb == 1), grpo=True)

        if now_row.path_file_audio == 'Unknown' and "audio" in modalities:
            continue
        
        question = ""
        modalities_tags = ""
        array_df = [None, None]
        if "symptoms" in modalities:
            row_dict = now_row._asdict()
            #selected_feats = random.sample(const_variable.columns_soundfeat, k=random.randint(3, len(const_variable.columns_soundfeat)))
            symptom_descriptions = ", ".join(
                f"{feat.replace('_', ' ')} is {row_dict[feat]}"
                for feat in const_variable.columns_soundfeat
                if row_dict.get(feat) != "Unknown"
            )
            if symptom_descriptions:
                question += f"The patient symptoms are {symptom_descriptions}."

        if "audio" in modalities:
            modalities_tags += "<audio>"
            array_df[0] = now_audiopath

        if "xray" in modalities:
            modalities_tags += "<image>"
            array_df[1] = now_imgaepath
            xray_descriptions = ", ".join(
                f"{feat.replace('_', ' ')} is {row_dict[feat]}"
                for feat in const_variable.columns_imagefeat
                if row_dict.get(feat) != "Unknown"
            )
            if xray_descriptions:
                question += f" The chest x-ray metadata are {xray_descriptions}."

        question = question.strip()
        question = question.rstrip(",.")
        if not question.endswith("."):
            question += "."

        question = modalities_tags + "" + question
        question += " " + last_sentence_question

        temp_instruct = {"messages": [
            {"role": "system",
                "content": [
                    {"type": "text", "text": system_prompt}
                ],
            },
            {
                "role": "user",
                "content": [
                    {"type": "text", "text": question},
                ],
            },
            {"role": "assistant", "content": [
                {"type": "text", "text": answer}]},
        ]}
        if array_df[0] != None:
            temp_instruct["messages"][1]['content'].append({"type": "audio", "audio": array_df[0]})
        if array_df[1] != None:
            temp_instruct["messages"][1]['content'].append({"type": "image", "image":array_df[1]})
        instruct_array_test.append(temp_instruct)

    test_instruct = commons.load_image_PIL(instruct_array_test)
    test_dataset = Dataset.from_list(commons.grpo_build_datasets(test_instruct, None))

    for temperature in [0.0, 0.5, 1.0]:
        adapter = f'{Checkpoint_PATH}/{Checkpoint_Number}'
        engine = PtEngine(model, adapters=adapter, max_batch_size=2)
        request_config = RequestConfig(max_tokens=512, temperature=temperature) # Kenapa 0, padahal di config 1
        
        resp_list = engine.infer(list(test_dataset), request_config)
        y_true = []
        y_pred= []
        for idx, resp_now in enumerate(resp_list):
            model_response = resp_now.choices[0].message.content
            y_pred.append(get_labelAnswer(model_response))
            y_true.append(get_labelAnswer(test_dataset[idx]['solution']))

        acc = accuracy_score(y_true, y_pred)
        cm = confusion_matrix(y_true, y_pred)
        tn, fp, fn, tp = cm.ravel()
        sensitivity = tp / (tp + fn) if (tp + fn) else 0
        specificity = tn / (tn + fp) if (tn + fp) else 0

        with open(f"{Checkpoint_PATH}/results_{temperature}.txt", "a") as f:
            f.write(f"Modalities: {modalities}\n")
            f.write(f"Accuracy: {acc:.4f}\n")
            f.write(f"Sensitivity: {sensitivity:.4f}\n")
            f.write(f"Specificity: {specificity:.4f}\n")
            f.write("Confusion Matrix:\n")
            f.write(str(cm) + "\n")
            f.write("-" * 40 + "\n")  # separator between runs

        del engine, request_config, resp_list
        import gc, torch
        gc.collect()
        torch.cuda.empty_cache()
        torch.cuda.ipc_collect()

In [17]:
%cd /home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni
import pickle, os, re, random, torch
from swift.llm import get_model_tokenizer, load_dataset, get_template, EncodePreprocessor
from swift.utils import get_logger, find_all_linears, get_model_parameter_info, plot_images, seed_everything
from swift.tuners import Swift, LoraConfig
from swift.trainers import Seq2SeqTrainer, Seq2SeqTrainingArguments
from datasets import Dataset
from functools import partial
import commons
import const_variable
import logging, warnings
class SuppressMultipleWarnings(logging.Filter):
    def filter(self, record):
        suppressed_msgs = [
            "Trainer.tokenizer is now deprecated",
            "System prompt modified, audio output may not work as expected"
        ]
        return not any(record.getMessage().startswith(msg) for msg in suppressed_msgs)
logging.getLogger().addFilter(SuppressMultipleWarnings())
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"

logger = get_logger()
seed_everything(42)

# Hyperparameters for training
os.environ.update({
    "MAX_PIXELS": "1003520",
    "NPROC_PER_NODE": "4",
    "ENABLE_AUDIO_OUTPUT": "0",
    "CUDA_VISIBLE_DEVICES": "0,1"
})

model_id_or_path = 'Qwen/Qwen2.5-Omni-3B'
output_dir = 'outputs/qwen25omni3b-think-balance-grpo'

data_seed = 42
max_length = 2048
split_dataset_ratio = 0.01  # Split validation set
num_proc = 4  # The number of processes for data loading.

# lora
lora_rank = 8
lora_alpha = 32

# training_args
training_args = Seq2SeqTrainingArguments(
    output_dir=output_dir,
    learning_rate=1e-4,
    per_device_train_batch_size=1,
    per_device_eval_batch_size=1,
    gradient_checkpointing=True,
    weight_decay=0.1,
    lr_scheduler_type='cosine',
    warmup_ratio=0.05,
    report_to=['tensorboard'],
    logging_first_step=True,
    save_strategy='steps',
    save_steps=50,
    eval_strategy='steps',
    eval_steps=50,
    gradient_accumulation_steps=16,
    num_train_epochs=1,
    metric_for_best_model='loss',
    save_total_limit=2,
    logging_steps=5,
    dataloader_num_workers=1,
    data_seed=data_seed,
)

output_dir = os.path.abspath(os.path.expanduser(output_dir))
logger.info(f'output_dir: {output_dir}')

# Obtain the model and template, and add a trainable Lora layer on the model.
model, tokenizer = get_model_tokenizer(model_id_or_path)
template = get_template(model.model_meta.template, tokenizer, default_system=const_variable.system_prompt, max_length=max_length)
template.set_mode('train')
if template.use_model:
    template.model = model

target_modules = find_all_linears(model)
lora_config = LoraConfig(task_type='CAUSAL_LM', r=lora_rank, lora_alpha=lora_alpha,
                         target_modules=target_modules)
model = Swift.prepare_model(model, lora_config)
logger.info(f'lora_config: {lora_config}')

# Print model structure and trainable parameters.
model_parameter_info = get_model_parameter_info(model)
logger.info(f'model_parameter_info: {model_parameter_info}')

/home/ldap-users-2/dwipraseetyo-a/Project/Qwen2.5-Omni


[INFO:swift] Successfully registered `/home/is/dwipraseetyo-a/.venv/lib/python3.12/site-packages/swift/llm/dataset/data/dataset_info.json`.
[INFO:swift] Global seed set to 42
[INFO:swift] output_dir: /home/ldap-users-2/dwipraseetyo-a/Project/Qwen2.5-Omni/outputs/qwen25omni3b-think-balance-grpo
[INFO:swift] Downloading the model from ModelScope Hub, model_id: Qwen/Qwen2.5-Omni-3B


[INFO:modelscope] Target directory already exists, skipping creation.
[INFO:swift] Loading the model using model_dir: /home/is/dwipraseetyo-a/.cache/modelscope/hub/models/Qwen/Qwen2___5-Omni-3B
Unrecognized keys in `rope_scaling` for 'rope_type'='default': {'mrope_section'}
[INFO:swift] Setting torch_dtype: torch.bfloat16
The image processor of type `Qwen2VLImageProcessor` is now loaded as a fast processor by default, even if the model checkpoint was saved with a slow processor. This is a breaking change and may produce slightly different outputs. To continue using the slow processor, instantiate this class with `use_fast=False`. Note that this behavior will be extended to all models in a future release.
You have video processor config saved in `preprocessor.json` file which is deprecated. Video processor configs should be saved in their own `video_preprocessor.json` file. You can rename the file or load and save the processor back which renames it automatically. Loading from `preproce

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

[INFO:swift] default_system: 'A conversation between User and Advanced medical assistant specialized in analyzing and diagnosing clinical conditions. and the Assistant determines whether the case is Positive or Negative. The assistant first thinks about the reasoning process in the mind and then provides the user with the answer. The reasoning process and answer are enclosed within <think> </think> and <answer> </answer> tags, respectively, i.e., <think> reasoning process here </think><answer> answer here </answer>'
[INFO:swift] max_length: 2048
[INFO:swift] response_prefix: ''
[INFO:swift] agent_template: hermes
[INFO:swift] norm_bbox: none
[INFO:swift] Setting use_audio_in_video: False. You can adjust this hyperparameter through the environment variable: `USE_AUDIO_IN_VIDEO`.
[INFO:swift] Setting sampling_rate: 16000. You can adjust this hyperparameter through the environment variable: `SAMPLING_RATE`.
/home/is/dwipraseetyo-a/.venv/lib/python3.12/site-packages/awq/__init__.py:21: Dep

In [1]:
%cd /home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni

import pickle, os, re, random, torch
from PIL import Image
from tqdm import tqdm
import commons
import const_variable
import copy
from qwen_omni_utils import process_mm_info
import io
import numpy as np
import soundfile as sf
from datasets import Dataset, concatenate_datasets
from swift.llm import get_model_tokenizer, load_dataset, get_template, EncodePreprocessor

/home/ldap-users-2/dwipraseetyo-a/Project/Qwen2.5-Omni


[INFO:swift] Successfully registered `/home/is/dwipraseetyo-a/.venv/lib/python3.12/site-packages/swift/llm/dataset/data/dataset_info.json`.


In [16]:
train_dataset, val_dataset = load_dataset(['lmms-lab/multimodal-open-r1-8k-verified#1000'], split_dataset_ratio=0.1, num_proc=8, use_hf=True)

[INFO:swift] Downloading the dataset from HuggingFace, dataset_id: lmms-lab/multimodal-open-r1-8k-verified


Map (num_proc=8):   0%|          | 0/7689 [00:00<?, ? examples/s]

Map (num_proc=8):   0%|          | 0/7689 [00:00<?, ? examples/s]

In [19]:
train_dataset[0]['messages']

[{'role': 'user',
  'content': "Based on the image, if segment DE is extended while maintaining the angle at point D constant, what will be the effect on the value of 's'? Choose the correct answer from the options below:\nChoices:\nA. Increase 's'\nB. Decrease 's'\nC. No change\nD. Make 's' negative"},
 {'role': 'assistant',
  'content': "<think>Let's consider the relationship between the length of segment DE and the value of 's'. The value of 's' is influenced by both the length of DE and the sine of the angle at point D. Since the angle remains constant, the sine of the angle does not change. Therefore, the only factor affecting 's' is the length of DE. As DE is extended, its length increases, which in turn increases the value of 's'. Hence, the correct answer is A.</think>\n\n<answer>A</answer>"}]

In [10]:
commons.pretty_status("📦 Loading Dataset...")

with open('datas/instruct_grpo_balance.pkl.train', 'rb') as f:
    train_instruct = commons.load_image_PIL(pickle.load(f))

with open('datas/instruct_grpo_balance.pkl.dev', 'rb') as f:
    dev_instruct = commons.load_image_PIL(pickle.load(f))
    
train_dataset = Dataset.from_list(commons.grpo_build_datasets(train_instruct, None)) #
val_dataset = Dataset.from_list(commons.grpo_build_datasets(dev_instruct, None))

combined = concatenate_datasets([train_dataset, val_dataset])
combined.push_to_hub("arkiven4/cirdz-instruct")


| 📦 Loading Dataset... |



  0%|                                                                                                                                                                                                               | 0/3526 [00:00<?, ?it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 439/439 [00:03<00:00, 121.75it/s]


Uploading the dataset shards:   0%|          | 0/4 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

CommitInfo(commit_url='https://huggingface.co/datasets/arkiven4/cirdz-instruct/commit/1f0bb74809c7e0c81df7c650fc3a4551b9095af2', commit_message='Upload dataset', commit_description='', oid='1f0bb74809c7e0c81df7c650fc3a4551b9095af2', pr_url=None, repo_url=RepoUrl('https://huggingface.co/datasets/arkiven4/cirdz-instruct', endpoint='https://huggingface.co', repo_type='dataset', repo_id='arkiven4/cirdz-instruct'), pr_revision=None, pr_num=None)

In [5]:
combined.features

{'messages': [{'content': Value(dtype='string', id=None),
   'role': Value(dtype='string', id=None)}],
 'solution': Value(dtype='string', id=None),
 'audios': Sequence(feature=Value(dtype='binary', id=None), length=-1, id=None),
 'images': [{'bytes': Value(dtype='binary', id=None),
   'path': Value(dtype='null', id=None)}]}

In [1]:
%cd /home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni

from datasets import load_from_disk
from datasets import DatasetDict

ds1 = load_from_disk('datas/hg_myown/train')
ds2 = load_from_disk('datas/hg_myown/val')

/home/ldap-users-2/dwipraseetyo-a/Project/Qwen2.5-Omni


⚠️  Warning: 'huggingface-cli login' is deprecated. Use 'hf auth login' instead.
The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `hf`CLI if you want to set the git credential as well.
Token is valid (permission: write).
The token `write1` has been saved to /home/is/dwipraseetyo-a/.cache/huggingface/stored_tokens
Your token has been saved to /home/is/dwipraseetyo-a/.cache/huggingface/token
Login successful.
The current active token is: `write1`


Uploading the dataset shards:   0%|          | 0/4 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

CommitInfo(commit_url='https://huggingface.co/datasets/arkiven4/cirdz-instruct/commit/36033d3c1361e8d48d88cfbcca9a767d5604ebc4', commit_message='Upload dataset', commit_description='', oid='36033d3c1361e8d48d88cfbcca9a767d5604ebc4', pr_url=None, repo_url=RepoUrl('https://huggingface.co/datasets/arkiven4/cirdz-instruct', endpoint='https://huggingface.co', repo_type='dataset', repo_id='arkiven4/cirdz-instruct'), pr_revision=None, pr_num=None)

In [19]:
from datasets import load_dataset

# Login using e.g. `huggingface-cli login` to access this dataset
ds = load_dataset("harryhsing/AVQA-R1-6K")

README.md:   0%|          | 0.00/851 [00:00<?, ?B/s]

AVQA_R1.tar.gz:   0%|          | 0.00/5.47G [00:00<?, ?B/s]

Generating train split: 0 examples [00:00, ? examples/s]

In [25]:
ds['train'][0]['wav']

{'path': 'AVQA_R1/valid/audios/sample_386.wav',
 'array': array([-0.06521606, -0.07067871, -0.07568359, ..., -0.00161743,
        -0.00149536, -0.00146484], shape=(512001,)),
 'sampling_rate': 44100}

In [13]:
lohe = commons.grpo_build_datasets(train_instruct, None)

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3526/3526 [00:31<00:00, 110.60it/s]


In [15]:
lohe[1]

{'messages': [{'role': 'system',
   'content': 'A conversation between User and Advanced medical assistant specialized in analyzing and diagnosing clinical conditions. and the Assistant determines whether the case is Positive or Negative. The assistant first thinks about the reasoning process in the mind and then provides the user with the answer. The reasoning process and answer are enclosed within <think> </think> and <answer> </answer> tags, respectively, i.e., <think> reasoning process here </think><answer> answer here </answer>'},
  {'role': 'user',
   'content': 'The patient symptoms are weight loss is no, hiv status is neg, sex is f, bmi is 37.0. The chest x-ray metadata are Modality is CR, ImagerPixelSpacing is [0.175, 0.175], Sensitivity is 250.0, PhotometricInterpretation is MONOCHROME2, Rows is 2434, Columns is 2010, WindowCenter is 2047.0, WindowWidth is 4096.0. Evaluate the x-ray, cough sound, and symptoms, is it Positive Tuberculosis or Negative Tuberculosis?. '},
  {'rol

In [12]:
train_instruct[1]

{'messages': [{'role': 'system',
   'content': [{'type': 'text',
     'text': 'A conversation between User and Advanced medical assistant specialized in analyzing and diagnosing clinical conditions. and the Assistant determines whether the case is Positive or Negative. The assistant first thinks about the reasoning process in the mind and then provides the user with the answer. The reasoning process and answer are enclosed within <think> </think> and <answer> </answer> tags, respectively, i.e., <think> reasoning process here </think><answer> answer here </answer>'}]},
  {'role': 'user',
   'content': [{'type': 'text',
     'text': 'The patient symptoms are weight loss is no, hiv status is neg, sex is f, bmi is 37.0. The chest x-ray metadata are Modality is CR, ImagerPixelSpacing is [0.175, 0.175], Sensitivity is 250.0, PhotometricInterpretation is MONOCHROME2, Rows is 2434, Columns is 2010, WindowCenter is 2047.0, WindowWidth is 4096.0. Evaluate the x-ray, cough sound, and symptoms, is

Saving the dataset (0/3 shards):   0%|          | 0/3526 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/439 [00:00<?, ? examples/s]

In [6]:
train_dataset[1]

{'messages': [{'content': 'A conversation between User and Advanced medical assistant specialized in analyzing and diagnosing clinical conditions. and the Assistant determines whether the case is Positive or Negative. The assistant first thinks about the reasoning process in the mind and then provides the user with the answer. The reasoning process and answer are enclosed within <think> </think> and <answer> </answer> tags, respectively, i.e., <think> reasoning process here </think><answer> answer here </answer>',
   'role': 'system'},
  {'content': 'The patient symptoms are weight loss is no, hiv status is neg, sex is f, bmi is 37.0. The chest x-ray metadata are Modality is CR, ImagerPixelSpacing is [0.175, 0.175], Sensitivity is 250.0, PhotometricInterpretation is MONOCHROME2, Rows is 2434, Columns is 2010, WindowCenter is 2047.0, WindowWidth is 4096.0. Evaluate the x-ray, cough sound, and symptoms, is it Positive Tuberculosis or Negative Tuberculosis?. ',
   'role': 'user'},
  {'con

In [93]:
from swift.llm import (
    get_model_tokenizer, load_dataset, get_template, EncodePreprocessor, get_model_arch,
    get_multimodal_target_regex, LazyLLMDataset
)

In [94]:
train_dataset = LazyLLMDataset(train_dataset, template.encode, random_state=data_seed)
val_dataset = LazyLLMDataset(val_dataset, template.encode, random_state=data_seed)

In [1]:
%cd /home/is/dwipraseetyo-a/NAS_HAI/Project/Qwen2.5-Omni
import pickle, os, re, random, torch
from peft import get_peft_model, LoraConfig, TaskType, get_peft_model_state_dict
from qwen_omni_utils import process_mm_info
from trl import SFTTrainer, SFTConfig, GRPOConfig, GRPOTrainer
from my_qwenwrapper import get_OmniModel
from sentence_transformers import SentenceTransformer, util

import commons
import const_variable
from my_datasets import QwenOmniFinetuneDataset

import logging, warnings
class SuppressMultipleWarnings(logging.Filter):
    def filter(self, record):
        suppressed_msgs = [
            "Trainer.tokenizer is now deprecated",
            "System prompt modified, audio output may not work as expected"
        ]
        return not any(record.getMessage().startswith(msg) for msg in suppressed_msgs)
logging.getLogger().addFilter(SuppressMultipleWarnings())

# warnings.filterwarnings("ignore", category=DeprecationWarning)
# warnings.filterwarnings("ignore", message="System prompt modified, audio output may not work as expected. Audio output mode only works when using default system prompt 'You are Qwen, a virtual human developed by the Qwen Team, Alibaba Group, capable of perceiving auditory and visual inputs, as well as generating text and speech.'")
# warnings.filterwarnings("ignore", message=r"Trainer\.tokenizer.*deprecated")
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


/home/ldap-users-2/dwipraseetyo-a/Project/Qwen2.5-Omni


In [2]:
model, processor = get_OmniModel(model_path="Qwen/Qwen2.5-Omni-3B", processor_path="Qwen/Qwen2.5-Omni-3B", padding_side="left",
                                use_flash_attention=True, only_processor=False, quantize_4bit=True, 
                                offload_folder="offload", set_eval=False)

Loading Processsor.... Using Left padding Side


The image processor of type `Qwen2VLImageProcessor` is now loaded as a fast processor by default, even if the model checkpoint was saved with a slow processor. This is a breaking change and may produce slightly different outputs. To continue using the slow processor, instantiate this class with `use_fast=False`. Note that this behavior will be extended to all models in a future release.
You have video processor config saved in `preprocessor.json` file which is deprecated. Video processor configs should be saved in their own `video_preprocessor.json` file. You can rename the file or load and save the processor back which renames it automatically. Loading from `preprocessor.json` will be removed in v5.0.


Loading Model.... Using BitsAndBytesConfig
Loading Model.... Using Offload Folder
Loading Model.... Using Flash Attention


Unrecognized keys in `rope_scaling` for 'rope_type'='default': {'mrope_section'}


Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

In [3]:
with open('datas/instruct_grpo_balance.pkl.dev', 'rb') as f:
    dev_instruct = commons.load_image_PIL(pickle.load(f))

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 439/439 [00:02<00:00, 153.29it/s]


In [26]:
conversation[1]['content']

[{'type': 'text',
  'text': 'The patient symptoms are body weight is 59.0, shortbreath is no. Given the cough audio and symptoms, is this case Positive Tuberculosis or Negative Tuberculosis?. '},
 {'type': 'audio', 'audio_start': 2.6, 'audio_end': 5.6}]

In [31]:
dev_datasets[0]

{'prompt': '<|im_start|>system\nA conversation between User and Advanced medical assistant specialized in analyzing and diagnosing clinical conditions. and the Assistant determines whether the case is Positive or Negative. The assistant first thinks about the reasoning process in the mind and then provides the user with the answer. The reasoning process and answer are enclosed within <think> </think> and <answer> </answer> tags, respectively, i.e., <think> reasoning process here </think><answer> answer here </answer><|im_end|>\n<|im_start|>user\nThe patient symptoms are shortbreath is no, tobacco use is never, height is 152.0, chestpain is no, night sweets is no, fever is no, hiv status is neg, sex is f, cough duration is no cough. The chest x-ray metadata are Modality is CR, ImagerPixelSpacing is [0.175, 0.175], Sensitivity is 250.0, PhotometricInterpretation is MONOCHROME2, Rows is 2446, Columns is 2010, WindowCenter is 2038.0, WindowWidth is 4096.0. Considering all inputs (image, so

In [16]:
print(prompt)

<|im_start|>system
A conversation between User and Advanced medical assistant specialized in analyzing and diagnosing clinical conditions. and the Assistant determines whether the case is Positive or Negative. The assistant first thinks about the reasoning process in the mind and then provides the user with the answer. The reasoning process and answer are enclosed within <think> </think> and <answer> </answer> tags, respectively, i.e., <think> reasoning process here </think><answer> answer here </answer><|im_end|>
<|im_start|>user
The patient symptoms are body weight is 59.0, shortbreath is no. Given the cough audio and symptoms, is this case Positive Tuberculosis or Negative Tuberculosis?. <|audio_bos|><|AUDIO|><|audio_eos|><|im_end|>
<|im_start|>assistant



In [21]:
print(solution)

<think>From the given symptoms and cough sound, Let me Analyze your regrading your questions.

## ⚠️ Points to Review and Disclaimer
* No X-ray Image Provided

This is a preliminary interpretation based on given data and does not replace a comprehensive clinical evaluation. A definitive diagnosis requires a additional clinical evaluation, including the physical examination findings, Cough Sound, Auscultation Sound, and imaging studies.
## 📋 Observations
**Symptoms:**
*   The symptoms provided do not support a diagnosis of Tuberculosis (TB). The patient has a productive cough lasting only 1-2 weeks, which is relatively short for TB, as the cough typically persists for months in TB cases. Additionally, the absence of hemoptysis, chest pain, shortness of breath, fever, night sweats, and weight loss further reduces the likelihood of TB, which often presents with these symptoms. The patient's negative HIV status and a healthy body mass index also support the absence of TB, given the higher 

In [ ]:
def multimodal_collate_fn(batch):
    prompts = []
    for sample in batch:
        conversation  = sample["messages"]
        for ele in conversation[1]['content']:
            if ele["type"] == "audio":
                if "audio" in ele or "audio_url" in ele:
                    path = ele.get("audio", ele.get("audio_url"))
                    start_sec, end_sec = commons.random_3sec_segment(path, segment_duration=3.0)
                    ele["audio_start"] = float(start_sec)
                    ele["audio_end"] = float(end_sec)
        prompt = processor.apply_chat_template(conversation, add_generation_prompt=True)
    return {
        "image": prompts,
        "image": prompts,
        "prompts": prompts,
        "solution": prompts,
    }

import re
from typing import Optional

def format_reward(completions, **kwargs):
    """Reward function that checks if the completion has a specific format."""
    pattern = r"^<think>\n.*?\n</think>\n<answer>\n.*?\n</answer>$"
    matches = [re.match(pattern, content, re.DOTALL | re.MULTILINE) for content in completions]
    rewards = [1.0 if match else 0.0 for match in matches]
    return rewards

def accuracy_reward(completions: list[list[dict[str, str]]], solution: list[str], **kwargs) -> list[Optional[float]]:
    """Reward function that checks if the completion matches the ground truth.
    - If both gold and prediction are parseable → use math verification.
    - If not parseable → compare as normalized text.
    """
    rewards = []
    for completion, sol in zip(completions, solution):
        reward = float(completion.strip().lower() == sol.strip().lower())
        rewards.append(reward)
    return rewards

##########################################################################################################
commons.pretty_status("🧠 Loading Model...")

peft_config = LoraConfig(task_type=TaskType.CAUSAL_LM, 
                        inference_mode=False, 
                        r=8, 
                        lora_alpha=32, 
                        lora_dropout=0.05, 
                        target_modules=["q_proj", "v_proj"])
                        #target_modules=["q_proj", "k_proj", "v_proj", "o_proj", "gate_proj", "up_proj", "down_proj"])

model, processor = get_OmniModel(model_path="Qwen/Qwen2.5-Omni-3B", processor_path="Qwen/Qwen2.5-Omni-3B", padding_side="left",
                                use_flash_attention=True, only_processor=False, quantize_4bit=True, 
                                offload_folder="offload", set_eval=False)

###
# How about we finetuning the audio and image encoder, not using PEFT, or increase PEFT to audio and image encoder

#model = prepare_model_for_kbit_training(model, use_gradient_checkpointing=True)
model.gradient_checkpointing_enable()
model.enable_input_require_grads()
peft_model = get_peft_model(model, peft_config)
peft_model.print_trainable_parameters()
model = peft_model.unload()
del peft_model

##########################################################################################################
commons.pretty_status("📦 Loading Dataset...")
with open('datas/instruct_grpo_balance.pkl.train', 'rb') as f:
    train_instruct = commons.load_image_PIL(pickle.load(f))

with open('datas/instruct_grpo_balance.pkl.dev', 'rb') as f:
    dev_instruct = commons.load_image_PIL(pickle.load(f))

train_dataset = QwenOmniFinetuneDataset(train_instruct, processor, use_audio_in_video=False)
dev_dataset = QwenOmniFinetuneDataset(dev_instruct, processor, use_audio_in_video=False)
print(train_dataset[0])
dataset = Dataset.from_list(instruct_array)

In [40]:
import pandas as pd
import numpy as np
import soundfile as sf
from pathlib import Path
import os
import librosa
import random
import pickle
import pydicom
import requests
import torch
import re
import shutil
from pydicom.datadict import keyword_for_tag
from transformers import AutoProcessor, AutoModelForImageTextToText, BitsAndBytesConfig
from IPython.display import Markdown, display
from openai import OpenAI
from PIL import Image
from tqdm import tqdm
from sklearn.utils import resample
import random
from itertools import combinations

import commons
import const_variable

from huggingface_hub import login
from dotenv import load_dotenv
from datasets import Dataset, concatenate_datasets

random.seed(42)

def sample_modalities_numeric_overlap(df, seed=42):
    random.seed(seed)
    np.random.seed(seed)

    # Only keep target diseases
    df = df[df['disease'].isin([1, 2, 4])].reset_index(drop=True)
    disease_classes = df['disease'].unique()
    augmented_rows = []

    for label in tqdm(disease_classes, desc="Processing disease classes"):
        class_df = df[df['disease'] == label].reset_index(drop=True)

        # Pools for sampling
        audio_rows = class_df[~class_df['path_file_audio'].isna()].reset_index(drop=True)
        image_rows = class_df[~class_df['path_file_image'].isna()].reset_index(drop=True)
        symptoms_rows = class_df[~class_df['symptoms_sentence'].isna()].reset_index(drop=True)

        for _, row in class_df.iterrows():
            base_audio = row['path_file_audio'] if pd.notna(row['path_file_audio']) else None
            base_image = row['path_file_image'] if pd.notna(row['path_file_image']) else None
            base_symp  = row['symptoms_sentence'] if pd.notna(row['symptoms_sentence']) else None

            # Sample fallback values if missing
            if base_audio is None and len(audio_rows) > 0:
                base_audio = audio_rows.sample(1, random_state=seed).iloc[0]['path_file_audio']
            if base_image is None and len(image_rows) > 0:
                base_image = image_rows.sample(1, random_state=seed).iloc[0]['path_file_image']
            if base_symp is None and len(symptoms_rows) > 0:
                base_symp = symptoms_rows.sample(1, random_state=seed).iloc[0]['symptoms_sentence']

            # Generate all 7 overlapping combos
            combos = {
                ("path_file_audio",): {"path_file_audio": base_audio, "path_file_image": None, "symptoms_sentence": None},
                ("path_file_image",): {"path_file_audio": None, "path_file_image": base_image, "symptoms_sentence": None},
                ("symptoms_sentence",): {"path_file_audio": None, "path_file_image": None, "symptoms_sentence": base_symp},
                ("path_file_audio", "path_file_image"): {"path_file_audio": base_audio, "path_file_image": base_image, "symptoms_sentence": None},
                ("path_file_audio", "symptoms_sentence"): {"path_file_audio": base_audio, "path_file_image": None, "symptoms_sentence": base_symp},
                ("path_file_image", "symptoms_sentence"): {"path_file_audio": None, "path_file_image": base_image, "symptoms_sentence": base_symp},
                ("path_file_audio", "path_file_image", "symptoms_sentence"): {"path_file_audio": base_audio, "path_file_image": base_image, "symptoms_sentence": base_symp},
            }

            for combo, vals in combos.items():
                new_row = row.to_dict()
                new_row.update(vals)
                new_row["modalities_used"] = combo
                augmented_rows.append(new_row)

    final_df = pd.DataFrame(augmented_rows).sample(frac=1, random_state=seed).reset_index(drop=True)
    return final_df

def sample_modalities_numeric(df, seed=42):
    df = df.sample(frac=1, random_state=seed).reset_index(drop=True)
    random.seed(seed)
    augmented_rows = []

    df = df[df['disease'].isin([1, 2, 4])].reset_index(drop=True)
    disease_classes = df['disease'].unique()

    for label in tqdm(disease_classes, desc="Processing disease classes"):
        class_df = df[df['disease'] == label].reset_index(drop=True)

        audio_rows = class_df[~class_df['path_file_audio'].isna()]
        image_rows = class_df[~class_df['path_file_image'].isna()]
        symptoms_rows = class_df[~class_df['symptoms_sentence'].isna()]

        combo_to_rows = {combo: [] for combo in [
            ("path_file_audio",),
            ("path_file_image",),
            ("symptoms_sentence",),
            ("path_file_audio", "path_file_image"),
            ("path_file_audio", "symptoms_sentence"),
            ("path_file_image", "symptoms_sentence"),
            ("path_file_audio", "path_file_image", "symptoms_sentence"),
        ]}

        for _, row in class_df.iterrows():
            base_modalities = {
                "path_file_audio": row['path_file_audio'] if pd.notna(row['path_file_audio']) else None,
                "path_file_image": row['path_file_image'] if pd.notna(row['path_file_image']) else None,
                "symptoms_sentence": row['symptoms_sentence'] if pd.notna(row['symptoms_sentence']) else None
            }
            all_combos = [
                ("path_file_audio",),
                ("path_file_image",),
                ("symptoms_sentence",),
                ("path_file_audio", "path_file_image"),
                ("path_file_audio", "symptoms_sentence"),
                ("path_file_image", "symptoms_sentence"),
                ("path_file_audio", "path_file_image", "symptoms_sentence"),
            ]
            for combo in all_combos:
                new_row = row.to_dict()
                for m in combo:
                    if base_modalities[m] is None:
                        if m == "path_file_audio" and len(audio_rows) > 0:
                            new_row[m] = audio_rows.sample(1, random_state=seed).iloc[0]['path_file_audio']
                        elif m == "path_file_image" and len(image_rows) > 0:
                            new_row[m] = image_rows.sample(1, random_state=seed).iloc[0]['path_file_image']
                        elif m == "symptoms_sentence" and len(symptoms_rows) > 0:
                            new_row[m] = symptoms_rows.sample(1, random_state=seed).iloc[0]['symptoms_sentence']
                    else:
                        new_row[m] = base_modalities[m]
                new_row["modalities_used"] = combo
                combo_to_rows[combo].append(new_row)

        min_count = min(len(rows)
                        for rows in combo_to_rows.values() if len(rows) > 0)
        for combo, rows in combo_to_rows.items():
            if not rows:
                continue
            sampled_rows = random.sample(rows, min_count)
            augmented_rows.extend(sampled_rows)

    final_df = pd.DataFrame(augmented_rows).sample(
        frac=1, random_state=seed).reset_index(drop=True)
    return final_df


disease_map = {
    "Others": 0,
    "Tuberculosis": 1,
    "Covid-19": 2
}
disease_map_reverse = {v: k for k, v in disease_map.items()}
prompt_templates = {
    ("audio",): [
        "Based on the cough audio provided,",
        "Evaluate the cough recording carefully,",
        "Consider the characteristics of this cough audio,",
        "From the recorded cough sound,",
        "Assess the features of the cough audio,",
        "Interpret the provided cough recording,",
        "Review the cough audio carefully,",
        "Examine the cough sound,"
    ],
    ("xray",): [
        "Based on the chest x-ray image,",
        "Evaluate the features seen in the x-ray,",
        "Interpret the chest radiograph,",
        "From the provided x-ray scan,",
        "Assess the chest x-ray image,",
        "Review the radiographic scan carefully,",
        "Examine the x-ray image,",
        "Consider the details in this chest x-ray,"
    ],
    ("symptoms",): [
        "Based on the reported symptoms,",
        "Evaluate the patient symptoms,",
        "Interpret the described symptom information,",
        "Review the presented symptoms,",
        "Assess the clinical symptoms carefully,",
        "Examine the provided symptom information,",
        "Consider the described symptoms,",
        "Analyze the symptom details,"
    ],
    ("audio", "xray"): [
        "Based on both the cough audio and chest x-ray,",
        "Evaluate the patient using cough audio and x-ray together,",
        "Interpret the cough recording along with the chest x-ray,",
        "Assess the x-ray and cough audio,",
        "Review the cough sound and chest x-ray together,",
        "Examine both the cough recording and x-ray image,",
        "Consider the x-ray alongside the cough audio,",
        "Analyze the combined cough audio and chest x-ray,"
    ],
    ("audio", "symptoms"): [
        "Based on the cough audio and reported symptoms,",
        "Evaluate the patient using cough audio and symptoms together,",
        "Interpret the cough recording along with the patient symptoms,",
        "Assess the cough sound and symptom description,",
        "Review the combined cough audio and symptoms,",
        "Examine both the cough recording and symptoms,",
        "Consider the cough audio alongside symptom information,",
        "Analyze the cough audio with the reported symptoms,"
    ],
    ("xray", "symptoms"): [
        "Based on the chest x-ray and reported symptoms,",
        "Evaluate the patient using x-ray and symptoms together,",
        "Interpret the chest x-ray along with the patient symptoms,",
        "Assess the x-ray and symptom details,",
        "Review the combined x-ray and symptom information,",
        "Examine both the chest radiograph and symptoms,",
        "Consider the x-ray image alongside the reported symptoms,",
        "Analyze the x-ray together with the symptom description,"
    ],
    ("audio", "xray", "symptoms"): [
        "Based on the cough audio, chest x-ray, and symptoms,",
        "Evaluate the patient using audio, x-ray, and symptoms together,",
        "Interpret the combined cough recording, x-ray, and symptom information,",
        "Assess all inputs: cough audio, x-ray, and symptoms,",
        "Review the cough sound, chest x-ray, and symptom details,",
        "Examine the cough audio, x-ray scan, and patient symptoms,",
        "Consider all data from audio, x-ray, and symptoms,",
        "Analyze the cough recording, x-ray image, and reported symptoms together,"
    ]
}

pseudo_cough_sentences_prefixed = {
    2: ["From this cough sound, the characteristics are dry, persistent, moderate number of coughs, mild hoarseness, intermittent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, hacking, frequent coughs, no hoarseness, persistent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, moderate frequency, mild hoarseness, persistent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, occasional coughs, no hoarseness, intermittent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, persistent, frequent, slight hoarseness, persistent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, hacking, moderate number of coughs, mild hoarseness, persistent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, persistent, few coughs, no hoarseness, intermittent pattern; this indicates COVID-19.",
        "From this cough sound, the characteristics are dry, persistent, moderate frequency, mild hoarseness, persistent pattern; this indicates COVID-19."],
    1: ["From this cough sound, the characteristics are wet, persistent, moderate number of coughs, mild hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, hacking, frequent coughs, mild hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, persistent, many coughs, moderate hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, hacking, few coughs, mild hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, persistent, moderate frequency, moderate hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, hacking, frequent coughs, mild hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, persistent, many coughs, moderate hoarseness, persistent pattern; this indicates TB.",
        "From this cough sound, the characteristics are wet, hacking, moderate number of coughs, mild hoarseness, persistent pattern; this indicates TB."],
    0: ["From this cough sound, the characteristics are occasional, mild, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are rare, mild, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are occasional, non-productive, mild hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are intermittent, mild, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are rare, non-specific, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are mild, occasional, no hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are intermittent, non-productive, mild hoarseness, intermittent pattern; this cannot determine a specific disease.",
        "From this cough sound, the characteristics are occasional, mild, no hoarseness, intermittent pattern; this cannot determine a specific disease."]
}

modalities_combinations = [
    ("path_file_audio",),
    ("path_file_image",),
    ("symptoms_sentence",),
    ("path_file_audio", "path_file_image"),
    ("path_file_audio", "symptoms_sentence"),
    ("path_file_image", "symptoms_sentence"),
    ("path_file_audio", "path_file_image", "symptoms_sentence"),
]

mod_map = {
    "path_file_audio": "audio",
    "path_file_image": "xray",
    "symptoms_sentence": "symptoms"
}

def map_modalities(row):
    return tuple(mod_map[m] for m in row if m in mod_map)


DATA_PATH = "/home/is/dwipraseetyo-a/NAS_HAI/Datasets"
DESTINATION_PATH = "/home/is/dwipraseetyo-a/NAS_HAI/Datasets/grpo_3modalities_datasets"

system_prompt = '''You are an advanced medical assistant AI specialized in analyzing and diagnosing clinical conditions. 
You can interpret auditory inputs, visual inputs, and patient symptoms, individually or in combination. 
Some inputs may be missing, and you should reason based on whatever is provided. 

Your task is to:
1. Analyze the available input(s): X-ray images if present, cough audio if present, and reported symptoms if present.   
2. Explain your reasoning step by step.  
3. Give the most likely diagnosis.  

Always respond in the following structured format, using the special tokens exactly as shown:

<think>
Analyze the available data, explain your reasoning, and show how you arrived at your conclusion.
</think>

<answer>
State the most likely disease or diagnosis.
</answer>'''

for split in ['val']:
    df1 = pd.read_csv(f"{DATA_PATH}/coda/metadata_llm.csv.{split}").rename(columns={
        "participant": "user_id", "tb_status": "disease", "path_file": "path_file_audio"})
    df1 = df1[['user_id', 'disease', 'path_file_audio',
               'symptoms_sentence', 'llm_analyze_symptoms']]
    df1["disease"] = df1["disease"].replace(0, 4)
    df1 = df1.groupby("user_id", group_keys=False).apply(
        lambda x: x.sample(n=min(len(x), 70), random_state=42)
    )
    df2 = pd.read_csv(f"{DATA_PATH}/ukcovid/metadata_llm.csv.{split}").rename(
        columns={"participant_identifier": "user_id", "covid_test_result": "disease"})
    df2["disease"] = df2["disease"].replace(1, 2)
    df2["disease"] = df2["disease"].replace(0, 4)
    df2 = df2[['user_id', 'disease', 'path_file_audio',
               'symptoms_sentence', 'llm_analyze_symptoms']]
    df3 = pd.read_csv(f"{DATA_PATH}/xray_metadata_llm_final.csv.{split}").rename(columns={
        "path_file": "path_file_image", "formatted_llm_analyze_image": "llm_analyze_image"})
    df_combined = pd.concat([df1, df2, df3], axis=0, ignore_index=True)
    
    if split == "val":
        split = "validation" 
        df_balanced = sample_modalities_numeric_overlap(df_combined)
        df_balanced['disease'] = df_balanced['disease'].replace({4: 0})
        df_balanced.reset_index(drop=True, inplace=True)
        df_balanced['modalities_simple'] = df_balanced['modalities_used'].apply(
            map_modalities)
        df_balanced.drop(['modalities_used'], axis=1, inplace=True) 

/tmp/ipykernel_3397339/137865647.py:305: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  df1 = df1.groupby("user_id", group_keys=False).apply(
Processing disease classes: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:05<00:00,  1.98s/it]


In [41]:
df_aug.groupby(['disease', 'modalities_used']).size()

disease  modalities_used                                      
1        (path_file_audio,)                                       15
         (path_file_audio, path_file_image)                       15
         (path_file_audio, path_file_image, symptoms_sentence)    15
         (path_file_audio, symptoms_sentence)                     15
         (path_file_image,)                                       15
         (path_file_image, symptoms_sentence)                     15
         (symptoms_sentence,)                                     15
2        (path_file_audio,)                                       15
         (path_file_audio, path_file_image)                       15
         (path_file_audio, path_file_image, symptoms_sentence)    15
         (path_file_audio, symptoms_sentence)                     15
         (path_file_image,)                                       15
         (path_file_image, symptoms_sentence)                     15
         (symptoms_sentence,)           

In [20]:
min_count = df_aug.groupby(['disease', 'modalities_used']).size().min()
df_balanced = (
    df_aug
    .groupby(['disease', 'modalities_used'], group_keys=False)
    .apply(lambda x: resample(x, replace=False, n_samples=min_count, random_state=42))
)
df_balanced['disease'] = df_balanced['disease'].replace({4: 0})
df_balanced['path_file_audio'] = df_balanced['path_file_audio'].apply(
    lambda x: f"{split}/{x.split('/')[-1]}" if pd.notna(x) else x)

df_balanced['path_file_image'] = df_balanced['path_file_image'].apply(
    lambda x: f"{split}/{x.split('/')[-1]}" if pd.notna(x) else x)
df_balanced.reset_index(drop=True, inplace=True)
df_balanced['modalities_simple'] = df_balanced['modalities_used'].apply(
    map_modalities)
df_balanced.drop(['modalities_used'], axis=1, inplace=True)

/tmp/ipykernel_3397339/2548786457.py:5: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(lambda x: resample(x, replace=False, n_samples=min_count, random_state=42))


In [21]:
df_balanced

user_id  disease  \
0      CODA_TB_0103        1   
1      CODA_TB_0469        1   
2      CODA_TB_0973        1   
3      ABOQ37E3R6JJ        1   
4      CA6J891WMOS6        1   
...             ...      ...   
16648      P0056824        0   
16649      P0052941        0   
16650  CODA_TB_0323        0   
16651      P0046070        0   
16652      P0034331        0   

                                         path_file_audio  \
0                      validation/l_CODA_TB_0103_291.wav   
1                     validation/l_CODA_TB_0469_3159.wav   
2                     validation/l_CODA_TB_0973_3424.wav   
3                     validation/l_CODA_TB_0469_2776.wav   
4                     validation/l_CODA_TB_0469_2776.wav   
...                                                  ...   
16648              validation/22746_CRMbNoqkMmOw8OFP.wav   
16649              validation/35118_DzArX4E7Z9TfnBMo.wav   
16650                    validation/l_CODA_TB_0323_4.wav   
16651  validation/71-13-df3b145b-c241-49d9-a6502e3629...   
16652              validation/50134_RXdUsFyXytaatBA7.wav   

                                       symptoms_sentence  \
0      smoke lweek is No, weight is 75.0, hiv status ...   
1      age is 42, weight is 54.0, hiv status is Negat...   
2      height is 154.0, weight is 48.0, hiv status is...   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
16648  age is 18-44, fever high temperature is no, ch...   
16649  new continuous cough is no, fatigue is no, hea...   
16650  night sweats is No, age is 38, smoke lweek is ...   
16651  gender is Female, abdominal pain is no, sore t...   
16652  cough any is no, age is 45-64, loss of taste i...   

                                    llm_analyze_symptoms  \
0      Based on the symptoms provided, the patient is...   
1      Based on the symptoms provided, the patient is...   
2      Based on the symptoms provided, the patient is...   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
16648  Based on the symptoms provided, the patient is...   
16649  Based on the symptoms provided, the patient is...   
16650  Based on the patient's symptoms and medical hi...   
16651  Based on the symptoms provided, the patient is...   
16652  Based on the symptoms provided, the patient is...   

                   path_file_image  \
0                              NaN   
1                              NaN   
2                              NaN   
3      validation/ABOQ37E3R6JJ.png   
4      validation/CA6J891WMOS6.png   
...                            ...   
16648                          NaN   
16649                          NaN   
16650                          NaN   
16651                          NaN   
16652                          NaN   

                                       llm_analyze_image modalities_simple  
0                                                    NaN          (audio,)  
1                                                    NaN          (audio,)  
2                                                    NaN          (audio,)  
3      The chest X-ray findings are suggestive of Tub...          (audio,)  
4      The chest X-ray findings are highly suggestive...          (audio,)  
...                                                  ...               ...  
16648                                                NaN       (symptoms,)  
16649                                                NaN       (symptoms,)  
16650                                                NaN       (symptoms,)  
16651                                                NaN       (symptoms,)  
16652                                                NaN       (symptoms,)  

[16653 rows x 8 columns]